# Development Right Transfers
#### Meeting Agenda: Development Rights Transfer & Conversion Analysis

1. Objectives & Data Review
    * Goal: Standardize ETL of transfer → conversion process & confirm data integration
    * Review analysis requirements
    * Review of data sources:
        * LT Info TDR Transactions (APN, type, land capability, quantity)
        * Parcel Master (jurisdiction, town center proximity, local plan)
        * Accela (transfer status, permit data)
2. Coding Plan & Standardization
    * Walkthrough of data integration approach
    * Confirm transfer first, then convert process
    * Address any inconsistencies or edge cases
3. Key Analyses
    * Land Capability: SEZ, sensitive, non-sensitive
    * Distance from Center: Trends by proximity
    * Interjurisdictional Activity: Transfers & conversions across boundaries
4. Next Steps
    * Assign action items & timeline for completion


## Notes: From Ken
- Transfer Reporting Status - comes from LTinfo
    - Transfers come out of LTinfo 
- Status of Transaction - comes from Accela
    - transaction is considered complete and development rights are moved to recieving parcel when the transfer is acknowledged
- Status of the Development on the Recieving Parcel
    - associate the transaction in LTinfo to the development project in Accela/Local Jurisdiction data
    - what is the status of the development project? (i.e. when is it existing on the ground)
 
- Transfer vs Conversion sequence
    - should be transfer dev rights then convert on the recieving parcel 
- Parcel Geneology Lookup needs to be built
    - Identify old APNs and current APNs
- Data Clean-up
    - categorization of unit types has evolved (e.g. PRUU vs RUU) same/same now
- Conversions
    - we track the transfers and then convert onto the recieving parcel (or onsite conversion)
    - track conversion net change
- 

## Setup

### Packages

In [1]:
import pandas as pd
import os
import pathlib
import arcpy
from arcgis.features import FeatureLayer, GeoAccessor, GeoSeriesAccessor
from utils import *
from datetime import datetime
from time import strftime  

### Global Variables

In [2]:
# set data frame display options
# pandas options
pd.options.mode.copy_on_write = True
pd.options.mode.chained_assignment = None
pd.options.display.max_columns = 999
pd.options.display.max_rows    = 999
pd.options.display.float_format = '{:,.2f}'.format
   
# set environement workspace to in memory 
arcpy.env.workspace = 'memory'
# overwrite true
arcpy.env.overwriteOutput = True
# Set spatial reference to NAD 1983 UTM Zone 10N
sr = arcpy.SpatialReference(26910)
arcpy.env.outputCoordinateSystem = sr

# current working directory
local_path = pathlib.Path().absolute()
# set data path as a subfolder of the current working directory TravelDemandModel\2022\
data_dir   = local_path.parents[0] / 'Reporting/data/raw_data'
# folder to save processed data
out_dir    = local_path.parents[0] / 'Reporting/data/processed_data'
# local geodatabase path
local_gdb = Path("C:\GIS\Scratch.gdb")
# network path to connection files
filePath = "F:/GIS/PARCELUPDATE/Workspace/"
# database file path 
sdeBase    = os.path.join(filePath, "Vector.sde")
sdeCollect = os.path.join(filePath, "Collection.sde")
sdeTabular = os.path.join(filePath, "Tabular.sde")
sdeEdit    = os.path.join(filePath, "Edit.sde")

## Data Processing
### Data Pipeline Overview
1. Extract data from LT Info, Parcel Master, and Accela.
2. Clean and preprocess data for consistency.
3. Merge datasets using APN as the primary key.
4. Standardize workflow: **transfer first, then convert**.
5. Identify and resolve inconsistencies.

### 1. Extract data from LT Info, Parcel Master, and Accela.

#### Data Sources
- **LT Info TDR Transactions**: Tracks APN, development right type, land capability, and quantity.
- **Parcel Master**: Provides jurisdiction, town center proximity, and
- **Accela**: Contains transfer status and permit details.

> Sources
* https://www.laketahoeinfo.org/WebServices/List
* https://maps.trpa.org/server/rest/services/
* https://parcels.laketahoeinfo.org/TdrTransaction/TransactionList
* sdeBase, sdeCollect, sdeTabular

#### 1.1 Parcel Master

In [3]:
# web service and database paths
# portal_ParcelMaster = 'https://maps.trpa.org/server/rest/services/Parcel_Master/FeatureServer/0'
sde_ParcelMaster    = Path(sdeBase) / "sde.SDE.Parcels\\sde.SDE.Parcel_Master"
# get spatially enabled dataframes
sdfParcels = pd.DataFrame.spatial.from_featureclass(sde_ParcelMaster)

c:\Users\amcclary\AppData\Local\ESRI\conda\envs\arcgispro-py3-plotly\Lib\site-packages\pandas\core\dtypes\cast.py:1066: RuntimeWarning: invalid value encountered in cast
  if (arr.astype(int) == arr).all():
c:\Users\amcclary\AppData\Local\ESRI\conda\envs\arcgispro-py3-plotly\Lib\site-packages\pandas\core\dtypes\cast.py:1091: RuntimeWarning: invalid value encountered in cast
  if (arr.astype(int) == arr).all():


#### 1.2 LTInfo Data

In [4]:
# transfer grid downloaded from LTinfo https://parcels.laketahoeinfo.org/TdrTransaction/TransactionList
# dfTransactionsGrid = pd.read_csv(local_path / "data/raw_data/TransactedAndBankedDevelopmentRights.csv")

# grid path
# dfTransactionsGrid = pd.read_excel(local_path / "data/raw_data/TdrTransactions as of 02_06_2025 12_00 PM.xlsx")
dfTransfers   = pd.read_excel(data_dir / "TdrTransactions as of 02_06_2025 12_00 PM.xlsx", sheet_name='Transfers')
dfConversions = pd.read_excel(data_dir / "TdrTransactions as of 02_06_2025 12_00 PM.xlsx", sheet_name='Conversions') 
dfConvTransfer = pd.read_excel(data_dir / "TdrTransactions as of 02_06_2025 12_00 PM.xlsx", sheet_name='Conversion with Transfers')

In [5]:
## LT Info Data
# get banked
dfDevRightBanked     = pd.read_json("https://www.laketahoeinfo.org/WebServices/GetBankedDevelopmentRights/JSON/e17aeb86-85e3-4260-83fd-a2b32501c476")
# Verified Development Rights from Accela as a DataFrame
dfDevRightForAccela  = pd.read_json("https://www.laketahoeinfo.org/WebServices/GetParcelDevelopmentRightsForAccela/JSON/e17aeb86-85e3-4260-83fd-a2b32501c476")
# Development Rights Transacted and Banked as a DataFrame
dfDevRightTransacted = pd.read_json("https://www.laketahoeinfo.org/WebServices/GetTransactedAndBankedDevelopmentRights/JSON/e17aeb86-85e3-4260-83fd-a2b32501c476")
# All Parcels as a DataFrame
dfLTParcel           = pd.read_json("https://www.laketahoeinfo.org/WebServices/GetAllParcels/JSON/e17aeb86-85e3-4260-83fd-a2b32501c476")

#### 1.3 Accela Permit Data

In [6]:
# API access to download excel file of Accela Record Details
accelaRecorDetails = "https://laketahoeinfo.org/Api/GetAccelaRecordDetailsExcel/1A77D078-B83E-44E0-8CA5-8D7429E1A6B4"
# download the file
dfAccelaRecord = pd.read_excel(accelaRecorDetails)

In [7]:
# get detailed project data report
dfDetailedProjectData = pd.read_excel(data_dir / "PermitStatusReport.xlsx")
dfDetailedProjectData.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 5409 entries, 0 to 5408
Data columns (total 8 columns):
 #   Column                  Non-Null Count  Dtype         
---  ------                  --------------  -----         
 0   File Number             5409 non-null   object        
 1   PARCEL NUMBER           5407 non-null   object        
 2   CURRENT PROJECT STATUS  5409 non-null   object        
 3   CATEGORY                5140 non-null   object        
 4   OPEN DATE               5409 non-null   datetime64[ns]
 5   Issued                  3876 non-null   datetime64[ns]
 6   Acknowledged            1691 non-null   datetime64[ns]
 7   Project Completed       883 non-null    datetime64[ns]
dtypes: datetime64[ns](4), object(4)
memory usage: 338.2+ KB


### 2. Clean and preprocess data for consistency.

In [8]:
final_schema = ['Transaction Status',
                'Transaction Type',
                'Development Right',
                'Sending Parcel APN',
                'Receiving Parcel APN',
                'Sending Quantity',
                'Receiving Quantity',
                'Sending Bailey Rating',
                'Receiving Bailey Rating',
                'Issued',
                'Acknowledged',
                'Project Completed', 
                'APN',
                'JURISDICTION',  
                'PLAN_TYPE',
                'LOCATION_TO_TOWNCENTER',
                'SHAPE']

### 3. Merge datasets using APN as the primary key.

In [9]:
# filter columns in sdf Parcels
parcels = sdfParcels[['APN', 'JURISDICTION', 'PLAN_TYPE', 'LOCATION_TO_TOWNCENTER', 'SHAPE']]
# merge dfTransfers with dfDetailedProjectData
df = pd.merge(dfTransfers, dfDetailedProjectData, left_on='Accela ID', right_on='File Number', how='left')
# merge Sending APN to Parcel APN
df = pd.merge(parcels, df, left_on='APN', right_on= 'Sending Parcel APN', how='inner')
# limit to final schema columns
df = df[final_schema]
# convert numeric columns to float
df['Sending Quantity'] = df['Sending Quantity'].astype(float)
df['Receiving Quantity'] = df['Receiving Quantity'].astype(float)
# export df to feature class
df.spatial.to_featureclass(local_gdb / "Parcel_Transfers", sanitize_columns=True, overwrite=True)

'C:\\GIS\\Scratch.gdb\\Parcel_Transfers'

In [10]:
# let's do this join twice once for the sending and once for the receiving
# merge dfTransfers with dfDetailedProjectData
df = pd.merge(dfTransfers, dfDetailedProjectData, left_on='Accela ID', right_on='File Number', how='left')

# merge Receiving APN to Parcel APN
dfRecieving = pd.merge(parcels, df, left_on='APN', right_on= 'Receiving Parcel APN', how='inner')
dfSending   = pd.merge(parcels, df, left_on='APN', right_on= 'Sending Parcel APN', how='inner')

# limit to final schema columns
dfRecieving = dfRecieving[final_schema]
dfSending   = dfSending[final_schema]

dfSending['Transaction Type'] = 'Sending'
dfRecieving['Transaction Type'] = 'Receiving'
dfSending['Net_Change'] = 0 - dfSending['Sending Quantity']
dfRecieving['Net_Change'] = dfRecieving['Receiving Quantity']

# group by APN, Development Right Type, and sum net change


# stack the two dataframes
df = pd.concat([dfRecieving, dfSending], axis=0, ignore_index=True)
df.spatial.to_featureclass(local_gdb / "Parcel_Transfers", sanitize_columns=True, overwrite=True)

'C:\\GIS\\Scratch.gdb\\Parcel_Transfers'

In [ ]:

# Check current CRS (spatial reference)
sr = parcels.spatial.sr
if sr and sr.wkid != 4326:  # Ensure it's in WGS84
    print(f"Reprojecting from EPSG:{sr.wkid} to EPSG:4326")

    # Convert to a feature class and reproject
    temp_fc = "in_memory\\temp_parcels"
    arcpy.management.Project(parcels.spatial.to_featureclass(location=temp_fc),
                             "in_memory\\parcels_wgs84",
                             arcpy.SpatialReference(4326))

    # Reload the reprojected feature class into an SEDF
    parcels = pd.DataFrame.spatial.from_featureclass("in_memory\\parcels_wgs84")

# Extract centroid as (x, y) tuple
parcels['centroid'] = parcels['SHAPE'].apply(lambda geom: geom.centroid)

# Extract longitude (X) and latitude (Y) from the tuple
parcels['long'] = parcels['centroid'].apply(lambda c: c[0])  # X-coordinate (longitude)
parcels['lat'] = parcels['centroid'].apply(lambda c: c[1])   # Y-coordinate (latitude)



Reprojecting from EPSG:26910 to EPSG:4326
cannot add field: 'centroid'
     long   lat
0 -119.94 39.32
1 -119.96 39.31
2 -119.91 39.30
3 -119.92 39.29
4 -119.92 39.30


In [31]:
# Create a dictionary from parcels DataFrame where APN is the key
apn_dict = parcels.set_index('apn')[['lat', 'long']].to_dict(orient='index')

# Function to lookup lat/long from the dictionary
def lookup_lat_long(apn):
    return apn_dict.get(apn, (None, None))  # Return None if APN not found

# Apply dictionary lookup to get receiving and sending lat/long
df['receiving_lat'], df['receiving_long'] = zip(*df['Receiving Parcel APN'].map(lookup_lat_long))
df['sending_lat'], df['sending_long'] = zip(*df['Sending Parcel APN'].map(lookup_lat_long))

# Display the result
print(df[['Receiving Parcel APN', 'receiving_lat', 'receiving_long', 'Sending Parcel APN', 'sending_lat', 'sending_long']].head())


  Receiving Parcel APN receiving_lat receiving_long Sending Parcel APN  \
0          112-280-009           lat           long        092-010-035   
1          090-231-014           lat           long        092-010-035   
2          090-231-014           lat           long        084-010-047   
3          031-123-020           lat           long        034-153-012   
4          032-282-016           lat           long        032-090-005   

  sending_lat sending_long  
0         lat         long  
1         lat         long  
2         lat         long  
3         lat         long  
4         lat         long  


In [48]:
# Create a dictionary from parcels DataFrame where APN is the key and (lat, long) is the value
apn_dict = parcels.set_index('apn')[['lat', 'long']].to_dict(orient='index')

# Function to lookup lat/long from the dictionary, and return as a tuple (lat, long)
def lookup_lat_long(apn):
    # Check if the APN exists in the dictionary and extract lat, long
    value = apn_dict.get(apn, {'lat': None, 'long': None})
    return value['lat'], value['long']  # Extract lat and long from the nested dictionary

# Apply the lookup function to get receiving lat/long
df['receiving_lat'], df['receiving_long'] = zip(*df['Receiving Parcel APN'].map(lookup_lat_long))

# Apply the lookup function to get sending lat/long
df['sending_lat'], df['sending_long'] = zip(*df['Sending Parcel APN'].map(lookup_lat_long))

# Display the result
print(df[['Receiving Parcel APN', 'receiving_lat', 'receiving_long', 'Sending Parcel APN', 'sending_lat', 'sending_long']].head())

#Drop records with null values in 'Sending lat or receiving lat' columns
df_sending_clean = df.dropna(subset=['sending_lat', 'receiving_long'])


  Receiving Parcel APN  receiving_lat  receiving_long Sending Parcel APN  \
0          112-280-009          39.26         -120.07        092-010-035   
1          090-231-014          39.23         -120.02        092-010-035   
2          090-231-014          39.23         -120.02        084-010-047   
3          031-123-020          38.92         -119.98        034-153-012   
4          032-282-016          38.90         -120.00        032-090-005   

   sending_lat  sending_long  
0        39.21       -120.11  
1        39.21       -120.11  
2        39.14       -120.18  
3        38.85       -120.00  
4        38.90       -119.99  


In [56]:
# html\4.1.d_commuter_percentage.html
import pydeck
def plot_commute_origin(df):
    # Still needs some formatting work
    GREEN_RGB = [0, 255, 0, 200]
    RED_RGB = [240, 100, 0, 200]

    arc_layer = pydeck.Layer(
        "ArcLayer",
        data=df,
        get_width="Receiving Quantity",
        get_source_position=["sending_long", "sending_lat"],
        get_target_position=["receiving_long", "receiving_lat"],
        get_tilt=15,
        get_source_color=RED_RGB,
        get_target_color=GREEN_RGB,
        pickable=True,
        auto_highlight=True,
    )

    view_state = pydeck.ViewState(
        latitude=38.8973752961, longitude=-120.007333471, bearing=45, pitch=50, zoom=8
    )

    tooltip = {"html": "{Receiving_Quantity} rights were sent from {SENDING_LOCATION_TO_TOWNCENTER} to {RECEIVING_LOCATION_TO_TOWNCENTER}<br /> Receiving in green; Sending in red"}
    r = pydeck.Deck(arc_layer, initial_view_state=view_state, tooltip=tooltip, map_style="road")

    r.to_html("parcel_transfer.html")

In [57]:
df_sending_clean['Receiving_Quantity'] = df_sending_clean['Receiving Quantity']

plot_commute_origin(df_sending_clean)

In [32]:
print (apn_dict)

{'048-041-03': {'lat': 39.32335638886909, 'long': -119.94432839123748}, '048-041-20': {'lat': 39.306568700681176, 'long': -119.96347458346979}, '048-042-02': {'lat': 39.297052928732114, 'long': -119.9096011238354}, '048-042-03': {'lat': 39.29198452605521, 'long': -119.92186047025314}, '048-140-03': {'lat': 39.29872996396747, 'long': -119.9219662186075}, '048-140-04': {'lat': 39.29740504020087, 'long': -119.93045432876842}, '055-010-07': {'lat': 39.29174407413118, 'long': -119.89708938968788}, '055-010-08': {'lat': 39.281346433913754, 'long': -119.89766403637545}, '055-010-09': {'lat': 39.2785003607567, 'long': -119.89395363762169}, '055-010-19': {'lat': 39.26217412744378, 'long': -119.8962693726034}, '055-010-25': {'lat': 39.238657996486864, 'long': -119.8986543845101}, '055-010-26': {'lat': 39.23142330928739, 'long': -119.89866516794132}, '122-051-01': {'lat': 39.25340051870111, 'long': -119.97328607182966}, '122-051-02': {'lat': 39.253084566284535, 'long': -119.97377242630621}, '122-

In [11]:
# merge dfTransfers with dfDetailedProjectData
df = pd.merge(dfTransfers, dfDetailedProjectData, left_on='Accela ID', right_on='File Number', how='left')
# merge Sending APN to Parcel APN
df = pd.merge(df, parcels, left_on='Sending Parcel APN', right_on='APN', how='left')
# rename parcels fields with prefix SENDING_
df.rename(columns={'JURISDICTION': 'SENDING_JURISDICTION', 'PLAN_TYPE': 'SENDING_PLAN_TYPE', 'LOCATION_TO_TOWNCENTER': 'SENDING_LOCATION_TO_TOWNCENTER'}, inplace=True)
# merge Receiving APN to Parcel APN
df = pd.merge(df, parcels, left_on='Receiving Parcel APN', right_on='APN', how='left')
# rename parcels fields with prefix RECEIVING_
df.rename(columns={'JURISDICTION': 'RECEIVING_JURISDICTION', 'PLAN_TYPE': 'RECEIVING_PLAN_TYPE', 'LOCATION_TO_TOWNCENTER': 'RECEIVING_LOCATION_TO_TOWNCENTER'}, inplace=True)

### 4. Standardize workflow: **transfer first, then convert**.

### 5. Identify and resolve inconsistencies.

In [ ]:
# APN changes over time

# Development Right name changed (e.g. RDR changed to PRUU)

# CTC and NDSL transactions will show up in the system later

# can be multiple transactions for the same APN and it could be the same development type
# transaction ID is unique so the many to many APN to transaction ID relationship can be used to join the data

## Key Analyses & Insights

### Land Capability Analysis
- Categorize transfers by SEZ, sensitive, and non-sensitive land.

In [12]:
df = df.copy()
# categorize
landcap_dict = {'1b':'SEZ',
                '1a':'Sensitive',
                '2':'Sensitive',
                '3':'Sensitive',
                '4':'Non-Sensitive',
                '5':'Non-Sensitive',
                '6':'Non-Sensitive',
                '7':'Non-Sensitive'}
# map land capability to land capability category
df['Sending_Land_Capability_Category'] = df['Sending Bailey Rating'].map(landcap_dict)
# map land capability to land capability category
df['Receiving_Land_Capability_Category'] = df['Receiving Bailey Rating'].map(landcap_dict)


In [14]:
# groupby sending_land_capability_category and receiving_land_capability_category
df_landcap_group = df.groupby(['Sending_Land_Capability_Category', 'Receiving_Land_Capability_Category', 'Development Right']).agg({
                                'Sending Quantity':'sum',
                                'Receiving Quantity': 'sum'}).reset_index()
df_landcap_group

Sending_Land_Capability_Category Receiving_Land_Capability_Category  \
0                     Non-Sensitive                      Non-Sensitive   
1                     Non-Sensitive                      Non-Sensitive   
2                     Non-Sensitive                      Non-Sensitive   
3                     Non-Sensitive                      Non-Sensitive   
4                     Non-Sensitive                      Non-Sensitive   
5                     Non-Sensitive                      Non-Sensitive   
6                     Non-Sensitive                      Non-Sensitive   
7                               SEZ                      Non-Sensitive   
8                               SEZ                      Non-Sensitive   
9                               SEZ                      Non-Sensitive   
10                              SEZ                      Non-Sensitive   
11                              SEZ                                SEZ   
12                              SEZ                                SEZ   
13                        Sensitive                      Non-Sensitive   
14                        Sensitive                      Non-Sensitive   
15                        Sensitive                      Non-Sensitive   

                                Development Right  Sending Quantity  \
0                     Commercial Floor Area (CFA)             70642   
1                                 Coverage (hard)             26392   
2                            Coverage (potential)             32756   
3    Multi-Family Residential Unit of Use (MFRUU)                 1   
4        Potential Residential Unit of Use (PRUU)                12   
5   Single-Family Residential Unit of Use (SFRUU)                59   
6                Tourist Accommodation Unit (TAU)               249   
7                                 Coverage (hard)            172080   
8                              Restoration Credit                62   
9   Single-Family Residential Unit of Use (SFRUU)                16   
10               Tourist Accommodation Unit (TAU)               105   
11                                Coverage (soft)              1098   
12                             Restoration Credit             29306   
13                    Commercial Floor Area (CFA)             10492   
14                                Coverage (hard)              7500   
15       Potential Residential Unit of Use (PRUU)                 2   

    Receiving Quantity  
0                70642  
1                26392  
2                32756  
3                    1  
4                   12  
5                   59  
6                  249  
7               141417  
8                   62  
9                   16  
10                 105  
11                1098  
12               29306  
13               10492  
14                5000  
15                   2

### Proximity Analysis
- Assess distance of transfers from town centers.

In [15]:
df_towncenter = df.groupby(['SENDING_LOCATION_TO_TOWNCENTER', 'RECEIVING_LOCATION_TO_TOWNCENTER', 'Development Right']).agg({
                                'Sending Quantity':'sum',
                                'Receiving Quantity': 'sum'}).reset_index() 
df_towncenter

SENDING_LOCATION_TO_TOWNCENTER            RECEIVING_LOCATION_TO_TOWNCENTER  \
0                  Outside Buffer  Further than Quarter Mile from Town Center   
1                  Outside Buffer                              Outside Buffer   
2                  Outside Buffer                              Outside Buffer   
3                  Outside Buffer                              Outside Buffer   
4                  Outside Buffer                              Outside Buffer   
5                  Outside Buffer                              Outside Buffer   
6                  Outside Buffer                              Outside Buffer   
7                  Outside Buffer                              Outside Buffer   
8                  Outside Buffer                         Quarter Mile Buffer   
9                  Outside Buffer                         Quarter Mile Buffer   
10                 Outside Buffer                         Quarter Mile Buffer   
11                 Outside Buffer                         Quarter Mile Buffer   
12                 Outside Buffer                         Quarter Mile Buffer   
13                 Outside Buffer                                 Town Center   
14                 Outside Buffer                                 Town Center   
15                 Outside Buffer                                 Town Center   
16                 Outside Buffer                                 Town Center   
17                 Outside Buffer                                 Town Center   
18            Quarter Mile Buffer                              Outside Buffer   
19            Quarter Mile Buffer                              Outside Buffer   
20            Quarter Mile Buffer                              Outside Buffer   
21            Quarter Mile Buffer                              Outside Buffer   
22            Quarter Mile Buffer                              Outside Buffer   
23            Quarter Mile Buffer                         Quarter Mile Buffer   
24            Quarter Mile Buffer                         Quarter Mile Buffer   
25            Quarter Mile Buffer                         Quarter Mile Buffer   
26            Quarter Mile Buffer                         Quarter Mile Buffer   
27            Quarter Mile Buffer                         Quarter Mile Buffer   
28            Quarter Mile Buffer                                 Town Center   
29            Quarter Mile Buffer                                 Town Center   
30            Quarter Mile Buffer                                 Town Center   
31            Quarter Mile Buffer                                 Town Center   
32            Quarter Mile Buffer                                 Town Center   
33            Quarter Mile Buffer                                 Town Center   
34            Quarter Mile Buffer                                 Town Center   
35                    Town Center                              Outside Buffer   
36                    Town Center                              Outside Buffer   
37                    Town Center                              Outside Buffer   
38                    Town Center                              Outside Buffer   
39                    Town Center                              Outside Buffer   
40                    Town Center                         Quarter Mile Buffer   
41                    Town Center                         Quarter Mile Buffer   
42                    Town Center                                 Town Center   
43                    Town Center                                 Town Center   
44                    Town Center                                 Town Center   
45                    Town Center                                 Town Center   
46                    Town Center                                 Town Center   

                                Development Right  Sending Quantity  \
0        Potential Residential Unit of Use 

### Interjurisdictional Transfers
- Examine development right transfers across jurisdictional boundaries.

In [16]:
# 
df_jurisdiction = df.groupby(['SENDING_JURISDICTION', 'RECEIVING_JURISDICTION', 'Development Right']).agg({
                                'Sending Quantity':'sum',
                                'Receiving Quantity': 'sum'}).reset_index() 
df_jurisdiction

SENDING_JURISDICTION RECEIVING_JURISDICTION  \
0                  CSLT                   CSLT   
1                  CSLT                   CSLT   
2                  CSLT                   CSLT   
3                  CSLT                   CSLT   
4                  CSLT                   CSLT   
5                  CSLT                   CSLT   
6                  CSLT                   CSLT   
7                  CSLT                   CSLT   
8                  CSLT                     DG   
9                  CSLT                     DG   
10                 CSLT                     EL   
11                 CSLT                     EL   
12                 CSLT                     EL   
13                 CSLT                     EL   
14                 CSLT                     EL   
15                 CSLT                     PL   
16                 CSLT                     PL   
17                 CSLT                     WA   
18                 CSLT                     WA   
19                 CSLT                     WA   
20                   DG                   CSLT   
21                   DG                   CSLT   
22                   DG                   CSLT   
23                   DG                     DG   
24                   DG                     DG   
25                   DG                     DG   
26                   DG                     DG   
27                   DG                     DG   
28                   DG                     DG   
29                   DG                     EL   
30                   DG                     EL   
31                   EL                   CSLT   
32                   EL                   CSLT   
33                   EL                   CSLT   
34                   EL                   CSLT   
35                   EL                   CSLT   
36                   EL                     EL   
37                   EL                     EL   
38                   EL                     EL   
39                   EL                     EL   
40                   EL                     EL   
41                   EL                     PL   
42                   EL                     WA   
43                   PL                   CSLT   
44                   PL                     EL   
45                   PL                     EL   
46                   PL                     EL   
47                   PL                     PL   
48                   PL                     PL   
49                   PL                     PL   
50                   PL                     PL   
51                   PL                     PL   
52                   PL                     WA   
53                   WA                   CSLT   
54                   WA                     WA   
55                   WA                     WA   
56                   WA                     WA   

                                Development Right  Sending Quantity  \
0                     Commercial Floor Area (CFA)             37339   
1                                 Coverage (hard)            164892   
2                            Coverage (potential)             30836   
3    Multi-Family Residential Unit of Use (MFRUU)                14   
4        Potential Residential Unit of Use (PRUU)                38   
5                              Restoration Credit              1208   
6   Single-Family Residential Unit of Use (SFRUU)                56   
7                Tourist Accommodation Unit (TAU)                40   
8        Potential Residential Unit of Use (PRUU)                 3   
9   Single-Family Residential Unit of Use (SFRUU)                 2   
10                                Coverage (hard)               946   
11                           Coverage (potential)              6582   
12       Potential Residential Unit of Use (PRUU)                 2   
13                             Restoration Credit             25402   
14  Single-Family Residential Unit of

## Next Steps
### Action Items
- Build Accela Report that gets us issued data 
- Get Accela ID and Jurisdiction Permit Number into LTinfo Web Service Development Rights Transacted and Banked
- Fix Parcel geneology for current 'APN', 'Recieving APN' and 'Sending APN' 